In [4]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sqlalchemy import create_engine
from sklearn import preprocessing
import mysql.connector
from pandas import DataFrame
from sklearn.metrics import jaccard_score
from numpy import logical_and as l_and, logical_not as l_not

In [5]:
disnet_db_ares = mysql.connector.connect(
  host="138.4.130.153",
  port = "30602",
  user="disnet_user",
  password="tYkX4JxV8p79",
  database="disnet_drugslayer"
)

 

disnet_mysql_cursor = disnet_db_ares.cursor()

In [6]:
def get_dummies(data,col_index,col_col):
    
    df_final= pd.get_dummies(data.set_index(col_index),col_col).reset_index()
    df_final=df_final.drop_duplicates()
    df_final=df_final.groupby(col_index).sum().reset_index()
    
    return df_final

def convert(lista):
    return tuple(i for i in lista)


def get_normal_diseases(rare_disease):
    '''
    Esta funcion devuelve un dataframe con la enfermedad, los medicamentos y los targets que son utiles
    para la enfermedad rara que se le pase como parametro'''
    
    
    q= f'''SELECT DISTINCT
        ds.disease_id, drug_name,dg.gene_id
        FROM
        disnet_biolayer.disease_gene dg 
        JOIN disnet_biolayer.disease ds ON ds.disease_id = dg.disease_id
        JOIN disnet_biolayer.encodes e_uno ON dg.gene_id = e_uno.gene_id
        JOIN disnet_drugslayer.has_code hc ON hc.code = e_uno.protein_id
        JOIN disnet_biolayer.ppi ppi on ppi.protein1_id = e_uno.protein_id
        JOIN disnet_biolayer.encodes e_dos on e_dos.protein_id = ppi.protein2_id
        JOIN disnet_drugslayer.drug_target dt ON hc.id = dt.target_id
        JOIN disnet_drugslayer.drug d ON dt.drug_id = d.drug_id
        WHERE
             hc.entity_id = 3
             
        and ds.ddf_type = "disease"
        and ppi.quality = "GOLD"
        AND dg.gene_id in (SELECT distinct(gene_id) FROM disnet_biolayer.disease_gene
        where disease_id = "{rare_disease}")
        ;'''
    
    df = pd.read_sql(q, con=disnet_db_ares)
    
    return df

In [9]:
rare_diseases= ['C0011195', 'C0023944', 'C0024054', 'C0024901', 'C0027877', 'C0036391', 'C0265202', 'C0268059', 'C0549463', 'C0751337', 'C0869083', 'C1852146', 'C0796280']
matrix_jac_ppi = pd.read_excel(("mat_jacc_pip.xlsx"),engine='openpyxl')
matrix_jac_ppi

rare_dis_id  C0000731  C0000737  C0000744  C0000768  C0000771  C0000772  \
0    C0011195         0         0         0  0.000000         0         0   
1    C0023944         0         0         0  0.000000         0         0   
2    C0024901         0         0         0  0.000000         0         0   
3    C0027877         0         0         0  0.000000         0         0   
4    C0036391         0         0         0  0.016949         0         0   
5    C0265202         0         0         0  0.017241         0         0   
6    C0549463         0         0         0  0.000000         0         0   
7    C0751337         0         0         0  0.000000         0         0   
8    C0869083         0         0         0  0.000000         0         0   

   C0000786  C0000822  C0000832  ...  C4540327  C4540342  C4540395  C4540493  \
0  0.023256  0.025641         0  ...         0         0         0         0   
1  0.000000  0.000000         0  ...         0         0         0         0   
2  0.000000  0.000000         0  ...         0         0         0         0   
3  0.000000  0.000000         0  ...         0         0         0         0   
4  0.000000  0.000000         0  ...         0         0         0         0   
5  0.000000  0.000000         0  ...         0         0         0         0   
6  0.000000  0.000000         0  ...         0         0         0         0   
7  0.000000  0.000000         0  ...         0         0         0         0   
8  0.000000  0.000000         0  ...         0         0         0         0   

   C4540496  C4540534  C4540535  C4540536  C4540602  C4545381  
0         0         0         0         0         0         0  
1         0         0         0         0         0         0  
2         0         0         0         0         0         0  
3         0         0         0         0         0         0  
4         0         0         0         0         0         0  
5         0         0         0         0         0         0  
6         0         0         0         0         0         0  
7         0         0         0         0         0         0  
8         0         0         0         0         0         0  

[9 rows x 12311 columns]

In [82]:
df_useful_diseases = get_normal_diseases("C0869083")
df_useful_diseases

disease_id           drug_name  gene_id
0      C0002448  SORAFENIB TOSYLATE      673
1      C0002448         VEMURAFENIB      673
2      C0002448           SORAFENIB      673
3      C0002448         REGORAFENIB      673
4      C0002448          DABRAFENIB      673
...         ...                 ...      ...
2710   C0699790        FOSTAMATINIB    22858
2711   C1306460        FOSTAMATINIB    22858
2712   C1691215        FOSTAMATINIB    22858
2713   C2675227        FOSTAMATINIB    22858
2714   C2981150        FOSTAMATINIB    22858

[2715 rows x 3 columns]

In [83]:
useful_diseases = get_normal_diseases("C0869083")['disease_id'].drop_duplicates().tolist()
len(useful_diseases)

352

In [84]:
df = matrix_jac_ppi[matrix_jac_ppi.rare_dis_id == 'C0869083']
df.head(2)

rare_dis_id  C0000731  C0000737  C0000744  C0000768  C0000771  C0000772  \
8    C0869083         0         0         0       0.0         0         0   

   C0000786  C0000822  C0000832  ...  C4540327  C4540342  C4540395  C4540493  \
8       0.0       0.0         0  ...         0         0         0         0   

   C4540496  C4540534  C4540535  C4540536  C4540602  C4545381  
8         0         0         0         0         0         0  

[1 rows x 12311 columns]

In [85]:
df_useful = df[['rare_dis_id'] + useful_diseases].set_index('rare_dis_id').transpose()
df_useful.sort_values(by='C0869083', ascending=False)

rare_dis_id  C0869083
C0346360     0.500000
C3263719     0.500000
C0019624     0.500000
C1275336     0.500000
C1332969     0.500000
...               ...
C0600139     0.001592
C0376358     0.001548
C2239176     0.001522
C0678222     0.001031
C0006142     0.001025

[352 rows x 1 columns]

In [86]:
df_normal_dis_jacc=pd.DataFrame(df_useful['C0869083'].nlargest(5)).reset_index().rename(columns={'index':'disease_id', 'C0869083':'jacc_idx'})

In [87]:
df_normal_dis_jacc.to_excel("dis_jacc_C0869083_ppi.xlsx")

In [88]:
df_normal_rare_drug=pd.merge(df_useful_diseases,df_normal_dis_jacc,on="disease_id",how="inner")

In [89]:
df_normal_rare_drug

disease_id            drug_name  gene_id  jacc_idx
0    C0019624   SORAFENIB TOSYLATE      673       0.5
1    C0019624          VEMURAFENIB      673       0.5
2    C0019624            SORAFENIB      673       0.5
3    C0019624          REGORAFENIB      673       0.5
4    C0019624           DABRAFENIB      673       0.5
5    C0019624         FOSTAMATINIB      673       0.5
6    C0019624  DABRAFENIB MESYLATE      673       0.5
7    C0019624          ENCORAFENIB      673       0.5
8    C0278600   SORAFENIB TOSYLATE      673       0.5
9    C0278600          VEMURAFENIB      673       0.5
10   C0278600            SORAFENIB      673       0.5
11   C0278600          REGORAFENIB      673       0.5
12   C0278600           DABRAFENIB      673       0.5
13   C0278600         FOSTAMATINIB      673       0.5
14   C0278600  DABRAFENIB MESYLATE      673       0.5
15   C0278600          ENCORAFENIB      673       0.5
16   C0278851   SORAFENIB TOSYLATE      673       0.5
17   C0278851          VEMURAFENIB      673       0.5
18   C0278851            SORAFENIB      673       0.5
19   C0278851          REGORAFENIB      673       0.5
20   C0278851           DABRAFENIB      673       0.5
21   C0278851         FOSTAMATINIB      673       0.5
22   C0278851  DABRAFENIB MESYLATE      673       0.5
23   C0278851          ENCORAFENIB      673       0.5
24   C0278882   SORAFENIB TOSYLATE      673       0.5
25   C0278882          VEMURAFENIB      673       0.5
26   C0278882            SORAFENIB      673       0.5
27   C0278882          REGORAFENIB      673       0.5
28   C0278882           DABRAFENIB      673       0.5
29   C0278882         FOSTAMATINIB      673       0.5
30   C0278882  DABRAFENIB MESYLATE      673       0.5
31   C0278882          ENCORAFENIB      673       0.5
32   C0334438   SORAFENIB TOSYLATE      673       0.5
33   C0334438          VEMURAFENIB      673       0.5
34   C0334438            SORAFENIB      673       0.5
35   C0334438          REGORAFENIB      673       0.5
36   C0334438           DABRAFENIB      673       0.5
37   C0334438         FOSTAMATINIB      673       0.5
38   C0334438  DABRAFENIB MESYLATE      673       0.5
39   C0334438          ENCORAFENIB      673       0.5

In [90]:
df_normal_rare_drug=df_normal_rare_drug.drop_duplicates()

In [91]:
prueba=df_normal_rare_drug.groupby('drug_name').count()

In [92]:
prueba

disease_id  gene_id  jacc_idx
drug_name                                         
DABRAFENIB                    5        5         5
DABRAFENIB MESYLATE           5        5         5
ENCORAFENIB                   5        5         5
FOSTAMATINIB                  5        5         5
REGORAFENIB                   5        5         5
SORAFENIB                     5        5         5
SORAFENIB TOSYLATE            5        5         5
VEMURAFENIB                   5        5         5

In [93]:
drug=prueba[prueba["disease_id"]>4]

In [94]:
drug

disease_id  gene_id  jacc_idx
drug_name                                         
DABRAFENIB                    5        5         5
DABRAFENIB MESYLATE           5        5         5
ENCORAFENIB                   5        5         5
FOSTAMATINIB                  5        5         5
REGORAFENIB                   5        5         5
SORAFENIB                     5        5         5
SORAFENIB TOSYLATE            5        5         5
VEMURAFENIB                   5        5         5

In [95]:
drug.to_excel("drugs_C0869083_ppi.xlsx")

In [96]:
drug_all=df_normal_rare_drug[df_normal_rare_drug["disease_id"]=="C0869083"]

In [97]:
drug_all

Empty DataFrame
Columns: [disease_id, drug_name, gene_id, jacc_idx]
Index: []

In [77]:
drug_all.to_excel("drugs_all_C0549463_ppi.xlsx")